<a href="https://colab.research.google.com/github/ClintonGJohnson/Coursera_Capstone/blob/main/Applied_Data_Science_Capstone_Week3_My_Submission.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Applied Data Science Capstone Week 3
## Peer Graded Assignment
### Segmenting and Clustering Neighbourhoods in Toronto

---
### Instructions

In this assignment, you will be required to explore, segment, and cluster the Neighbourhoods in the city of Toronto based on the postalcode and borough information.. However, unlike New York, the Neighbourhood data is not readily available on the internet. What is interesting about the field of data science is that each project can be challenging in its unique way, so you need to learn to be agile and refine the skill to learn new libraries and tools quickly depending on the project.

For the Toronto Neighbourhood data, a Wikipedia page exists that has all the information we need to explore and cluster the Neighbourhoods in Toronto. You will be required to scrape the Wikipedia page and wrangle the data, clean it, and then read it into a pandas  dataframe so that it is in a structured format like the New York dataset.

Once the data is in a structured format, you can replicate the analysis that we did to the New York City dataset to explore and cluster the Neighbourhoods in the city of Toronto.

Your submission will be a link to your Jupyter Notebook on your Github repository.


---
### My Approach


1.   **Compile a list (DataFrame df) of neighbourhoods in Toronto**

> Gather the list of neighbourhood names and coordinates (latitude and longitude of neighbourhood centroids)


> Clean the list removing rows or columns with missing data



2.   **Compile a list of venues near each neighbourhood** (within 500 meters of the centroid, which may lead to overlaps in some cases and may not encompass the full Neighbourhood in other cases)

3. **Analyze Each Neighbourhood**

4. **Cluster Neighbourhoods**

5. **Examine Clusters**







### Install and import relevant libraries
* Pandas
* Numpy
* SciKit-Learn
* MatPlotLib
* GeoPy
* Json

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
#from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

/bin/bash: conda: command not found
Libraries imported.


# 1. Compile a list (DataFrame df) of neighbourhoods in Toronto
> Gather the list of neighbourhood names and coordinates (latitude and longitude of neighbourhood centroids)
> 1. **Gather Neighbourhood List from Wiki page:** https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M&oldid=945633050.
> The first Table in the web page contains a list of Neighbourhoods in Toronto
> 2. **Clean the list** removing rows or columns with missing data
> Remove any records with "Not Assigned" Burough or Neighbourhood
> 3. **Geocode each neighbourhood** to collect coordinates

## 1.1. **Gather Neighbourhood List from Wiki page:**

In [2]:
url = "https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M&oldid=945633050"
html_tables = pd.read_html(url)

html_tables[0].head() # confirming that we have the correct table (Columns: Postcode, Borough, Neighbourhood)

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

## **1.2**. **Clean the list**

In [3]:
df = html_tables[0] # set the DataFrame df
# replace "Not Assigned" with None
df = df.replace({'Not assigned':None})
df.count()

Postcode         287
Borough          210
Neighbourhood    210
dtype: int64

In [4]:
# drop nulls (Nones)
df.dropna(axis=0, inplace=True)
df.count()

Postcode         210
Borough          210
Neighbourhood    210
dtype: int64

Explore the list

In [5]:
df.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M6A        North York  Lawrence Heights
6      M6A        North York    Lawrence Manor

In [6]:
df.shape

(210, 3)

# 2. Geocode Neighborhoods

## 2.1. Install Esri's ArcGIS Python Libraries
> Using Esri's ArcGIS Online for reliable and accurate geocoding

In [13]:
!pip install arcgis # Using Esri's ArcGIS for accurate geocoding
#!conda install -c esri arcgis

## 2.2. Configuring Geocoder

In [7]:
from arcgis.gis import GIS
from arcgis.geocoding import Geocoder, get_geocoders, geocode


from IPython.display import display

arcgis_online = GIS()
items = arcgis_online.content.search('Geocoder', 'geocoding service', max_items=3)
    
# construct a geocoder using the first geocoding service item
worldgeocoder = Geocoder.fromitem(items[0])
worldgeocoder   

<Geocoder url:"https://geocoder.arcgisonline.nl/arcgis/rest/services/Geocoder_BAG_RD/GeocodeServer">

## 2.3. Geocode each neighbourhood

In [10]:
address_format = "{}, {}, ON, CA" # Neighbourhood, Borough, ON, CA

toronto_data = pd.DataFrame(columns=['Postcode', 'Borough', 'Neighbourhood', 'Address', 'Latitude', 'Longitude'])
no_match = 0
matched = 0

for p, b, n in zip(df['Postcode'], df['Borough'], df['Neighbourhood']):
  address = address_format.format(n,b)
  print('Geocoding {}'.format( address))

  latitude = None
  longitude = None
  location = None

  try: 
    matches = geocode(address) #Geocode using ArcGIS Online
    if len(matches)>0:
      location = matches[0]
  except TimeoutError:
    print('Geocoder Request Timed Out')
  except:
    print('Error has occurred')

  if location == None:
    no_match+=1
    print('...No results :(')
  else:
    latitude = location['location']['y']
    longitude = location['location']['x']
    matched+=1
    print('...{}, {}'.format(latitude,longitude))

  toronto_data = toronto_data.append(
      {
        'Address': address,
        'Latitude': latitude,
        'Longitude': longitude,
        'Neighbourhood': n,
        'Borough': b,
        'Postcode': p
      },
      ignore_index=True
  )

print('Geocoding Complete! {} locations matched, but {} not matched'.format(matched, no_match))

toronto_data.shape

Geocoding Parkwoods, North York, ON, CA
...44.20973226495906, -79.47189723748289
Geocoding Victoria Village, North York, ON, CA
...43.73154000000005, -79.31427999999994
Geocoding Harbourfront, Downtown Toronto, ON, CA
...43.65011000000004, -79.38289999999995
Geocoding Lawrence Heights, North York, ON, CA
...43.72357000000005, -79.43710999999996
Geocoding Lawrence Manor, North York, ON, CA
...43.72294000000005, -79.43115999999998
Geocoding Queen's Park, Downtown Toronto, ON, CA
...43.660673101153115, -79.39083464301146
Geocoding Islington Avenue, Etobicoke, ON, CA
...43.738221166575215, -79.56573343932973
Geocoding Rouge, Scarborough, ON, CA
...43.807660000000055, -79.17404999999997
Geocoding Malvern, Scarborough, ON, CA
...43.81023000000005, -79.22037999999998
Geocoding Don Mills North, North York, ON, CA
...43.705685127473515, -79.33385691603588
Geocoding Woodbine Gardens, East York, ON, CA
...43.70626000000004, -79.30090999999999
Geocoding Parkview Hill, East York, ON, CA
...43.70464

(210, 6)

Review the data

In [12]:
toronto_data.head(11)

Postcode           Borough     Neighbourhood  \
0       M3A        North York         Parkwoods   
1       M4A        North York  Victoria Village   
2       M5A  Downtown Toronto      Harbourfront   
3       M6A        North York  Lawrence Heights   
4       M6A        North York    Lawrence Manor   
5       M7A  Downtown Toronto      Queen's Park   
6       M9A         Etobicoke  Islington Avenue   
7       M1B       Scarborough             Rouge   
8       M1B       Scarborough           Malvern   
9       M3B        North York   Don Mills North   
10      M4B         East York  Woodbine Gardens   

                                   Address   Latitude  Longitude  
0            Parkwoods, North York, ON, CA  44.209732 -79.471897  
1     Victoria Village, North York, ON, CA  43.731540 -79.314280  
2   Harbourfront, Downtown Toronto, ON, CA  43.650110 -79.382900  
3     Lawrence Heights, North York, ON, CA  43.723570 -79.437110  
4       Lawrence Manor, North York, ON, CA  43.722940 -79.431160  
5   Queen's Park, Downtown Toronto, ON, CA  43.660673 -79.390835  
6      Islington Avenue, Etobicoke, ON, CA  43.738221 -79.565733  
7               Rouge, Scarborough, ON, CA  43.807660 -79.174050  
8             Malvern, Scarborough, ON, CA  43.810230 -79.220380  
9      Don Mills North, North York, ON, CA  43.705685 -79.333857  
10     Woodbine Gardens, East York, ON, CA  43.706260 -79.300910

# 3. **Compile a list of venues near each neighbourhood** 
> Use FourSquare to find venues within 500 meters of each Neighbourhood location (centroid)
> Using centroids may lead to overlaps in some cases and may not encompass the full Neighbourhood in other **cases**

## 3.1. Set FourSquare Credentials 
```{danger} Protect Your Client ID, Secret, & Access Token
The following cell contains the FourSquare Client ID, Client Secret, and Access Token used by this app.
```

In [ ]:
#@title Default title text
CLIENT_ID = 'E1XXDLPD4CE2W2XTFQGFHDN15UXV2DS11OEMYS3V5EUVRQCC' # your Foursquare ID
CLIENT_SECRET = '3MKNWT3BVIQ3D2I2UM22BTJM2DELZXQTZK4X52F2BNDCBLS2' # your Foursquare Secret
ACCESS_TOKEN = 'SAU3DU2THQH0ILF41QTNII1UCHSN4XZJN2DJ5CKPTALRWBH0' # your FourSquare Access Token

VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)
#https://foursquare.com/oauth2/authenticate?client_id=E1XXDLPD4CE2W2XTFQGFHDN15UXV2DS11OEMYS3V5EUVRQCC&response_type=code&redirect_uri=https://www.google.com
#https://foursquare.com/oauth2/access_token?client_id=E1XXDLPD4CE2W2XTFQGFHDN15UXV2DS11OEMYS3V5EUVRQCC&client_secret=3MKNWT3BVIQ3D2I2UM22BTJM2DELZXQTZK4X52F2BNDCBLS2&grant_type=authorization_code&redirect_uri=https://www.google.com&code=TNEFVDXJGNE1I2WUQLKVP0DVHHPM5Y5D4BSB2DNFTSJJECJM#_=_

In [15]:
toronto_data.head()

Postcode           Borough     Neighbourhood  \
0      M3A        North York         Parkwoods   
1      M4A        North York  Victoria Village   
2      M5A  Downtown Toronto      Harbourfront   
3      M6A        North York  Lawrence Heights   
4      M6A        North York    Lawrence Manor   

                                  Address   Latitude  Longitude  
0           Parkwoods, North York, ON, CA  44.209732 -79.471897  
1    Victoria Village, North York, ON, CA  43.731540 -79.314280  
2  Harbourfront, Downtown Toronto, ON, CA  43.650110 -79.382900  
3    Lawrence Heights, North York, ON, CA  43.723570 -79.437110  
4      Lawrence Manor, North York, ON, CA  43.722940 -79.431160

In [16]:
toronto_data.dtypes

Postcode          object
Borough           object
Neighbourhood     object
Address           object
Latitude         float64
Longitude        float64
dtype: object

In [17]:
latitude = toronto_data.iloc[1]['Latitude']
longitude = toronto_data.iloc[1]['Longitude']
radius = 500
format_me = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'
url = format_me.format(CLIENT_ID, CLIENT_SECRET, 
                       latitude, longitude, 
                       VERSION, 
                       radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?client_id=E1XXDLPD4CE2W2XTFQGFHDN15UXV2DS11OEMYS3V5EUVRQCC&client_secret=3MKNWT3BVIQ3D2I2UM22BTJM2DELZXQTZK4X52F2BNDCBLS2&ll=43.73154000000005,-79.31427999999994&v=20180604&radius=500&limit=30'

## 3.2. Create a function to find (explore) nearby venues

---



In [18]:
def getNearbyVenues(boroughs, neighbourhoods, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for borough, neighbourhood, lat, lng in zip(boroughs, neighbourhoods, latitudes, longitudes):
        print("Getting venues around {}, {}".format(borough, neighbourhood))
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        #results = requests.get(url).json()["response"]['venues']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            borough, 
            neighbourhood, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Borough', 'Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

## 3.3. Run the function for each Neighbourhood in Toronto

In [19]:
venues = getNearbyVenues(
    toronto_data['Borough'], 
    toronto_data['Neighbourhood'], 
    toronto_data['Latitude'],     
    toronto_data['Longitude'], 
    radius=500)

Getting venues around North York, Parkwoods
Getting venues around North York, Victoria Village
Getting venues around Downtown Toronto, Harbourfront
Getting venues around North York, Lawrence Heights
Getting venues around North York, Lawrence Manor
Getting venues around Downtown Toronto, Queen's Park
Getting venues around Etobicoke, Islington Avenue
Getting venues around Scarborough, Rouge
Getting venues around Scarborough, Malvern
Getting venues around North York, Don Mills North
Getting venues around East York, Woodbine Gardens
Getting venues around East York, Parkview Hill
Getting venues around Downtown Toronto, Ryerson
Getting venues around Downtown Toronto, Garden District
Getting venues around North York, Glencairn
Getting venues around Etobicoke, Cloverdale
Getting venues around Etobicoke, Islington
Getting venues around Etobicoke, Martin Grove
Getting venues around Etobicoke, Princess Gardens
Getting venues around Etobicoke, West Deane Park
Getting venues around Scarborough, Hig

In [20]:
print("Located {} venues around {} Neighbourhoods".format(venues.shape[0], toronto_data.shape[0]))
venues.head()

Located 2938 venues around 210 Neighbourhoods


Borough Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  North York     Parkwoods               44.209732               -79.471897   
1  North York     Parkwoods               44.209732               -79.471897   
2  North York     Parkwoods               44.209732               -79.471897   
3  North York     Parkwoods               44.209732               -79.471897   
4  North York     Parkwoods               44.209732               -79.471897   

                    Venue  Venue Latitude  Venue Longitude     Venue Category  
0          Tom and Gerrys       44.207839       -79.470798        Wings Joint  
1     Glenwood Beach Park       44.208892       -79.475198               Lake  
2              Pine Beach       44.212609       -79.470350              Beach  
3                Circle K       44.209016       -79.466987  Convenience Store  
4  Keswick Auto Glass Inc       44.213552       -79.471299    Automotive Shop

Let's check how many venues were returned for each Neighbourhood

In [21]:
venues[['Neighbourhood','Venue']].groupby('Neighbourhood').count()

Venue
Neighbourhood                                           
Adelaide                                              30
Agincourt                                             20
Agincourt North                                       28
Albion Gardens                                         4
Alderwood                                              5
Bathurst Manor                                         4
Bathurst Quay                                         28
Bayview Village                                        4
Beaumond Heights                                       5
Bedford Park                                           7
Berczy Park                                           30
Birch Cliff                                            2
Bloordale Gardens                                      4
Brockton                                              30
Business Reply Mail Processing Centre 969 Eastern     30
CFB Toronto                                           30
CN Tower                                              30
Cabbagetown                                           30
Caledonia-Fairbanks                                    2
Canada Post Gateway Processing Centre                 16
Cedarbrae                                              4
Central Bay Street                                    30
Chinatown                                             30
Christie                                              30
Church and Wellesley                                  30
Clairlea                                               4
Clarks Corners                                        10
Cliffcrest                                             8
Cliffside                                              9
Cliffside West                                         9
Cloverdale                                            22
Commerce Court                                        30
Davisville                                            19
Davisville North                                      19
Deer Park                                             30
Del Ray                                               25
Design Exchange                                       30
Don Mills North                                        4
Don Mills South                                        4
Dorset Park                                           12
Dovercourt Village                                    30
Downsview                                              6
Downsview Central                                      6
Downsview East                                         6
Downsview North                                        6
Downsview Northwest                                    6
Downsview West                                         6
Dufferin                                              10
East Birchmount Park                                   4
East Toronto                                          30
Emery                                                  2
Eringate                                               5
Exhibition Place                                      27
Fairview                                              15
First Canadian Place                                  30
Flemingdon Park                                       14
Forest Hill North                                      5
Forest Hill SE                                         4
Forest Hill West                                       4
Garden District                                       30
Glencairn                                              5
Golden Mile                                           27
Grange Park                                           30
Guildwood                                              2
Harbord                                               30
Harbourfront                                          30
Harbourfront East                                     30
Harbourfront West                                     30
Henry Farm                                             5
High

Let's check how many venues were returned for each borough

In [22]:
venues[['Borough','Venue']].groupby('Borough').count()

Venue
Borough                
Central Toronto     263
Downtown Toronto   1072
East Toronto        151
East York            59
Etobicoke           382
Mississauga          16
North York          261
Scarborough         317
West Toronto        317
York                100

Let's find out how many unique categories can be curated from all the returned venues


In [23]:
print('There are {} uniques categories.'.format(len(venues['Venue Category'].unique())))

There are 278 uniques categories.


# 4. Analyze Each Neighbourhood


## 4.1. Generate One Hot analysis

In [24]:
# one hot encoding
toronto_onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot.head()

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0                  0               0                  0                   0   
1                  0               0                  0                   0   
2                  0               0                  0                   0   
3                  0               0                  0                   0   
4                  0               0                  0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  American Restaurant  Amphitheater  Antique Shop  \
0                 0                    0             0             0   
1                 0                    0             0             0   
2                 0                    0             0             0   
3                 0                    0             0             0   
4                 0                    0             0             0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0            0                    0                 0                   0   
1            0                    0                 0                   0   
2            0                    0                 0                   0   
3            0                    0                 0                   0   
4            0                    0                 0                   0   

   Auto Garage  Automotive Shop  BBQ Joint  Badminton Court  Bagel Shop  \
0            0                0          0                0           0   
1            0                0          0                0           0   
2            0                0          0                0           0   
3            0                0          0                0           0   
4            0                1          0                0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Stadium  Beach  Beer Bar  \
0       0     0    0               0                   0      0         0   
1       0     0    0               0                   0      0         0   
2       0     0    0               0                   0      1         0   
3       0     0    0               0                   0      0         0   
4       0     0    0               0                   0      0         0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  \
0           0                   0          0       0              0   
1           0                   0          0       0              0   
2           0                   0          0       0              0   
3           0                   0          0       0              0   
4           0                   0          0       0              0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0            0       0                0         0             0   
1            0       0                0         0             0   
2            0       0                0         0             0   
3            0       0                0         0             0   
4            0       0                0         0             0   

   Burrito Place  Bus Line  Bus Station  Bus S

In [25]:
# add Neighbourhood column back to dataframe
toronto_onehot['zzNeighbourhood'] = venues['Neighbourhood'] 

# move borough and n column to the first columns
fixed_columns = [toronto_onehot.columns[-1]] +  list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.rename(columns={"zzNeighbourhood": "Neighbourhood"}, inplace=True)
toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Parkwoods                  0               0                  0   
1     Parkwoods                  0               0                  0   
2     Parkwoods                  0               0                  0   
3     Parkwoods                  0               0                  0   
4     Parkwoods                  0               0                  0   

   African Restaurant  Airport  Airport Food Court  Airport Lounge  \
0                   0        0                   0               0   
1                   0        0                   0               0   
2                   0        0                   0               0   
3                   0        0                   0               0   
4                   0        0                   0               0   

   Airport Service  Airport Terminal  American Restaurant  Amphitheater  \
0                0                 0                    0             0   
1                0                 0                    0             0   
2                0                 0                    0             0   
3                0                 0                    0             0   
4                0                 0                    0             0   

   Antique Shop  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0            0                    0                 0   
1             0            0                    0                 0   
2             0            0                    0                 0   
3             0            0                    0                 0   
4             0            0                    0                 0   

   Athletics & Sports  Auto Garage  Automotive Shop  BBQ Joint  \
0                   0            0                0          0   
1                   0            0                0          0   
2                   0            0                0          0   
3                   0            0                0          0   
4                   0            0                1          0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0           0       0     0    0               0   
1                0           0       0     0    0               0   
2                0           0       0     0    0               0   
3                0           0       0     0    0               0   
4                0           0       0     0    0               0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Belgian Restaurant  \
0                   0      0         0           0                   0   
1                   0      0         0           0                   0   
2                   0      1         0           0                   0   
3                   0      0         0           0                   0   
4                   0      0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0               0        0            0       0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0              0        

In [26]:
# add borough column back to dataframe
toronto_onehot['Borough'] = venues['Borough'] 

# move borough and n column to the first columns
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Borough Neighbourhood  Accessories Store  Adult Boutique  \
0  North York     Parkwoods                  0               0   
1  North York     Parkwoods                  0               0   
2  North York     Parkwoods                  0               0   
3  North York     Parkwoods                  0               0   
4  North York     Parkwoods                  0               0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  0                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Amphitheater  Antique Shop  Art Gallery  Arts & Crafts Store  \
0             0             0            0                    0   
1             0             0            0                    0   
2             0             0            0                    0   
3             0             0            0                    0   
4             0             0            0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Automotive Shop  \
0                 0                   0            0                0   
1                 0                   0            0                0   
2                 0                   0            0                0   
3                 0                   0            0                0   
4                 0                   0            0                1   

   BBQ Joint  Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0                0           0       0     0    0               0   
1          0                0           0       0     0    0               0   
2          0                0           0       0     0    0               0   
3          0                0           0       0     0    0               0   
4          0                0           0       0     0    0               0   

   Basketball Stadium  Beach  Beer Bar  Beer Store  Belgian Restaurant  \
0                   0      0         0           0                   0   
1                   0      0         0           0                   0   
2                   0      1         0           0                   0   
3                   0      0         0           0                   0   
4                   0      0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0               0        0            0       0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0 

And let's examine the new dataframe size.

In [27]:
toronto_onehot.shape

(2938, 280)

## 4.2. Group rows by Neighbourhood and Assess frequency of occurrence of each category
>Next, let's group rows by Neighbourhood and by taking the mean of the frequency of occurrence of each category

### 4.2.1. Group by Neighbourhood

In [28]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                             Adelaide           0.000000   
1                                            Agincourt           0.000000   
2                                      Agincourt North           0.000000   
3                                       Albion Gardens           0.000000   
4                                            Alderwood           0.000000   
5                                       Bathurst Manor           0.000000   
6                                        Bathurst Quay           0.000000   
7                                      Bayview Village           0.000000   
8                                     Beaumond Heights           0.000000   
9                                         Bedford Park           0.000000   
10                                         Berczy Park           0.000000   
11                                         Birch Cliff           0.000000   
12                                   Bloordale Gardens           0.000000   
13                                            Brockton           0.000000   
14   Business Reply Mail Processing Centre 969 Eastern           0.000000   
15                                         CFB Toronto           0.000000   
16                                            CN Tower           0.000000   
17                                         Cabbagetown           0.000000   
18                                 Caledonia-Fairbanks           0.000000   
19               Canada Post Gateway Processing Centre           0.000000   
20                                           Cedarbrae           0.000000   
21                                  Central Bay Street           0.000000   
22                                           Chinatown           0.000000   
23                                            Christie           0.000000   
24                                Church and Wellesley           0.000000   
25                                            Clairlea           0.000000   
26                                      Clarks Corners           0.000000   
27                                          Cliffcrest           0.000000   
28                                           Cliffside           0.000000   
29                                      Cliffside West           0.000000   
30                                          Cloverdale           0.000000   
31                                      Commerce Court           0.000000   
32                                          Davisville           0.000000   
33                                    Davisville North           0.000000   
34                                           Deer Park           0.000000   
35                                             Del Ray           0.000000   
36                                     Design Exchange           0.000000   
37                                     Don Mills North           0.000000   
38                                     Don Mills South           0.000000   
39                                         Dorset Park           0.000000   
40                                  Dovercourt Village           0.000000   
41                                           Downsview           0.000000   
42                                   Downsview Central           0.000000   
43                                      Downsview East           0.000000   
44                                     Downsview North           0.000000   
45                                 Downsview Northwest           0.000000   
46                                      Downsview West           0.000000   
47                                            Dufferin           0.000000   
48                                East Birchmount Park           0.000000   
49                                        East Toronto           0.000000   
50                                               Emery           0.000000   
51                                   

#### Let's confirm the new size

In [29]:
toronto_grouped.shape

(202, 279)

### 4.2.2. Determine Top 5 Common Venue Categories
> Let's print each Neighbourhood along with the top 5 most common venues

In [30]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
                 venue  freq
0  American Restaurant  0.10
1                 Café  0.10
2          Coffee Shop  0.10
3   Seafood Restaurant  0.07
4     Asian Restaurant  0.07


----Agincourt----
                  venue  freq
0    Chinese Restaurant  0.20
1      Asian Restaurant  0.15
2            Food Court  0.10
3  Cantonese Restaurant  0.10
4   Rental Car Location  0.05


----Agincourt North----
                venue  freq
0                Bank  0.07
1              Bakery  0.07
2  Chinese Restaurant  0.07
3         Men's Store  0.04
4          Beer Store  0.04


----Albion Gardens----
                 venue  freq
0         Hockey Arena  0.25
1  Fried Chicken Joint  0.25
2          Auto Garage  0.25
3             Gym Pool  0.25
4               Museum  0.00


----Alderwood----
                venue  freq
0   Convenience Store   0.2
1         Pizza Place   0.2
2        Dance Studio   0.2
3  Athletics & Sports   0.2
4         Coffee Shop   0.2


----Bathurst Manor----
   

#### Let's put that into a _pandas_ dataframe


First, let's write a function to sort the venues in descending order.

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each Neighbourhood.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
Neighbourhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    Neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

Neighbourhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide           Coffee Shop                  Café   
1        Agincourt    Chinese Restaurant      Asian Restaurant   
2  Agincourt North                Bakery                  Bank   
3   Albion Gardens          Hockey Arena              Gym Pool   
4        Alderwood          Dance Studio           Pizza Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0   American Restaurant                   Gym      Asian Restaurant   
1            Food Court  Cantonese Restaurant  Hong Kong Restaurant   
2    Chinese Restaurant        Ice Cream Shop            Beer Store   
3           Auto Garage   Fried Chicken Joint  Fast Food Restaurant   
4     Convenience Store           Coffee Shop    Athletics & Sports   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
0     Seafood Restaurant            Restaurant       Gluten-free Restaurant   
1  Vietnamese Restaurant                Bakery                Shopping Mall   
2             Restaurant   Fried Chicken Joint           Frozen Yogurt Shop   
3         Farmers Market                  Farm                        Field   
4            Event Space   Dumpling Restaurant  Eastern European Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0            Steakhouse                 Bakery  
1           Coffee Shop      Korean Restaurant  
2             Juice Bar         Discount Store  
3    Falafel Restaurant        Doctor's Office  
4     Electronics Store            Escape Room

# 5. Cluster Neighbourhoods

# 6. Examine Clusters


Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster.

## 6.1. Cluster 0

In [40]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Longitude  Cluster Labels       1st Most Common Venue  \
0         North York -79.471897             0.0             Automotive Shop   
9         North York -79.333857             0.0           Convenience Store   
19         Etobicoke -79.557420             0.0           Convenience Store   
20       Scarborough -79.176140             0.0  Construction & Landscaping   
22       Scarborough -79.131090             0.0                    Bus Line   
24        North York -79.333857             0.0           Convenience Store   
27              York -79.426980             0.0                     Dog Run   
29         Etobicoke -79.578240             0.0          Chinese Restaurant   
33       Scarborough -79.205230             0.0                 Coffee Shop   
34       Scarborough -79.178200             0.0                Home Service   
39         East York -79.351065             0.0              Sandwich Place   
44        North York -79.454770             0.0                  Playground   
68        North York -79.379570             0.0                       Trail   
80       Scarborough -79.279120             0.0             Motorcycle Shop   
90        North York -79.500031             0.0          Mexican Restaurant   
102             York -79.483674             0.0      Furniture / Home Store   
112  Central Toronto -79.444179             0.0               Grocery Store   
118      Scarborough -79.276940             0.0               Deli / Bodega   
121  Central Toronto -79.427450             0.0                         Spa   
122  Central Toronto -79.424670             0.0                     Dog Run   
138        Etobicoke -79.537990             0.0               Moving Target   
145     West Toronto -79.470553             0.0          Light Rail Station   
150  Central Toronto -79.488754             0.0                        Park   
159  Central Toronto -79.424670             0.0                     Dog Run   
162  Central Toronto -79.488754             0.0                        Park   
171        Etobicoke -79.493032             0.0           Indian Restaurant   
178        Etobicoke -79.599814             0.0                        Pool   
187      Scarborough -79.187694             0.0                Home Service   
198        Etobicoke -79.493840             0.0                        Park   
200        Etobicoke -79.493032             0.0           Indian Restaurant   
203        Etobicoke -79.495482             0.0                        Park   
206        Etobicoke -79.493032             0.0           Indian Restaurant   
208        Etobicoke -79.495482             0.0                        Park   

          2nd Most Common Venue       3rd Most Common Venue  \
0                         Beach                 Wings Joint   
9                 Hot Dog Joint                        Park   
19                Movie Theater                       Hotel   
20                         Park                Neighborhood   
22                Train Station                        Park   
24                Hot Dog Joint                        Park   
27                 Hockey Arena                       Field   
29                  Pizza Place           Convenience Store   
33                         Park              Sandwich Place   
34            Convenience Store                        Park   
39            Indian Restaurant                        Park   
44            Convenience Store                        Park   
68                      Dog Run  Construction & Landscaping   
80                        Trail                    Bus Stop   
90        Vietnamese Restaurant                       Trail   
102                 Gas Station                        Park   
112        Caribbean Restaurant           Convenience Store   
118  Construction & Landscaping            Business Service   
121                       Trail                        Park   
122                       Field                       Trail   
138

## 6.2. Cluster 1

In [41]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Longitude  Cluster Labels      1st Most Common Venue  \
4          North York -79.431160             1.0                Pizza Place   
6           Etobicoke -79.565733             1.0          Indian Restaurant   
7         Scarborough -79.174050             1.0                Gas Station   
8         Scarborough -79.220380             1.0       Fast Food Restaurant   
14         North York -79.446449             1.0                     Bakery   
16          Etobicoke -79.565733             1.0          Indian Restaurant   
28          Etobicoke -79.570740             1.0             Discount Store   
31          Etobicoke -79.579884             1.0                Pizza Place   
38        Scarborough -79.228290             1.0          Indian Restaurant   
45         North York -79.499895             1.0                Pizza Place   
46         North York -79.434170             1.0                   Pharmacy   
47          East York -79.343530             1.0         Turkish Restaurant   
52       West Toronto -79.448672             1.0                   Bus Line   
53        Scarborough -79.216990             1.0                Coffee Shop   
61   Downtown Toronto -79.377150             1.0                Pizza Place   
70         North York -79.499895             1.0                Pizza Place   
72       East Toronto -79.559982             1.0                Supermarket   
83         North York -79.499895             1.0                Pizza Place   
85       East Toronto -79.565510             1.0          Indian Restaurant   
88         North York -79.499895             1.0                Pizza Place   
92        Scarborough -79.232970             1.0             Ice Cream Shop   
93        Scarborough -79.250623             1.0          Fish & Chips Shop   
94        Scarborough -79.216990             1.0                Coffee Shop   
97         North York -79.499895             1.0                Pizza Place   
103              York -79.495520             1.0       Fast Food Restaurant   
104              York -79.461092             1.0      Vietnamese Restaurant   
108       Scarborough -79.250623             1.0          Fish & Chips Shop   
110        North York -79.499895             1.0                Pizza Place   
114              York -79.483374             1.0                Coffee Shop   
125         Etobicoke -79.519480             1.0                Pizza Place   
127       Scarborough -79.299558             1.0  Middle Eastern Restaurant   
136         Etobicoke -79.558775             1.0                Pizza Place   
139         Etobicoke -79.531230             1.0                Pizza Place   
144      West Toronto -79.483707             1.0                Coffee Shop   
146       Scarborough -79.301560             1.0      Vietnamese Restaurant   
148       Scarborough -79.298330             1.0                Pizza Place   
176         Etobicoke -79.585498             1.0              Grocery Store   
177         Etobicoke -79.594659             1.0                Pizza Place   
180         Etobicoke -79.564140             1.0          Indian Restaurant   
184         Etobicoke -79.541160             1.0               Dance Studio   
186         Etobicoke -79.750671             1.0                Pizza Place   

    2nd Most Common Venue       3rd Most Common Venue  4th Most Common Venue  \
4        Department Store              Breakfast Spot             Bagel Shop   
6    Caribbean Restaurant                 Coffee Shop                   Bank   
7             Pizza Place                Intersection            Bus Station   
8             Pizza Place                    Pharmacy         Sandwich Place   
14            Pizza Place            Asian Restaurant    Japanese Restaurant   
16   Caribbean Restaurant                 Coffee Shop                   Bank   
28            Pizza Place        Fast Food Restaurant                   Bank   
31      Convenience Store                    Pharmacy  

## 6.3 Cluster 2

In [42]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Longitude  Cluster Labels 1st Most Common Venue  \
1         North York -79.314280             2.0                  Park   
3         North York -79.437110             2.0                  Park   
17         Etobicoke -79.553895             2.0         Jewelry Store   
32       Scarborough -79.189920             2.0                  Park   
37              York -79.454830             2.0         Women's Store   
42       Scarborough -79.235178             2.0                  Park   
43        North York -79.353460             2.0                  Park   
66       Scarborough -79.273200             2.0                  Park   
95        North York -79.409830             2.0                  Park   
128       North York -79.428020             2.0     Mobile Phone Shop   
149  Central Toronto -79.437935             2.0                  Park   
174        Etobicoke -79.570586             2.0                  Park   
194        Etobicoke -79.495493             2.0                  Park   
199        Etobicoke -79.503383             2.0                  Park   
201        Etobicoke -79.495493             2.0                  Park   
205        Etobicoke -79.503383             2.0                  Park   

                        2nd Most Common Venue 3rd Most Common Venue  \
1                                         Zoo  Ethiopian Restaurant   
3                           Accessories Store  Ethiopian Restaurant   
17                                       Park                   Zoo   
32                                      Hotel                   Zoo   
37                                       Park                   Zoo   
42                              Grocery Store            Playground   
43   Residential Building (Apartment / Condo)                   Zoo   
66                                        Zoo  Ethiopian Restaurant   
95                                        Zoo  Ethiopian Restaurant   
128                                      Park                   Zoo   
149                               Coffee Shop                   Zoo   
174                              Skating Rink                Bakery   
194                                       Spa   American Restaurant   
199                                Kids Store                 River   
201                                       Spa   American Restaurant   
205                                Kids Store                 River   

    4th Most Common Venue 5th Most Common Venue        6th Most Common Venue  \
1        Doner Restaurant   Dumpling Restaurant  Eastern European Restaurant   
3        Doner Restaurant   Dumpling Restaurant  Eastern European Restaurant   
17        Doctor's Office      Doner Restaurant          Dumpling Restaurant   
32   Ethiopian Restaurant      Doner Restaurant          Dumpling Restaurant   
37   Ethiopian Restaurant      Doner Restaurant          Dumpling Restaurant   
42   Ethiopian Restaurant               Dog Run             Doner Restaurant   
43        Doctor's Office      Doner Restaurant          Dumpling Restaurant   
66       Doner Restaurant   Dumpling Restaurant  Eastern European Restaurant   
95       Doner Restaurant   Dumpling Restaurant  Eastern European Restaurant   
128  Ethiopian Restaurant      Doner Restaurant          Dumpling Restaurant   
149  Ethiopian Restaurant      Doner Restaurant          Dumpling Restaurant   
174      Business Service      Doner Restaurant  Eastern European Restaurant   
194         Metro Station           Event Space          Dumpling Restaurant   
199     Electronics Store       Doctor's Office                      Dog Run   
201         Metro Station           Event Space          Dumpling Restaurant   
205     Electronics Store       Doctor's Office                      Dog Run   

           7th Most Common Venue        8th Most Common Venue  \
1              Electronics Store                  Escape Room   
3              Electronics Store                  Escape Room   
17   Ea

## 6.3. Cluster 3

In [43]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Longitude  Cluster Labels  \
2    Downtown Toronto -79.382900             3.0   
5    Downtown Toronto -79.390835             3.0   
10          East York -79.300910             3.0   
11          East York -79.322670             3.0   
12   Downtown Toronto -79.382900             3.0   
13   Downtown Toronto -79.382900             3.0   
15          Etobicoke -79.556136             3.0   
18          Etobicoke -79.542556             3.0   
23         North York -79.331710             3.0   
26   Downtown Toronto -79.373590             3.0   
35       East Toronto -79.296440             3.0   
36   Downtown Toronto -79.382900             3.0   
40   Downtown Toronto -79.387556             3.0   
41   Downtown Toronto -79.382900             3.0   
48   Downtown Toronto -79.382900             3.0   
49   Downtown Toronto -79.382900             3.0   
50   Downtown Toronto -79.382900             3.0   
51       West Toronto -79.430364             3.0   
54         North York -79.257546             3.0   
55         North York -79.340860             3.0   
56         North York -79.203085             3.0   
57         North York -79.496470             3.0   
58         North York -79.498630             3.0   
59          East York -79.469200             3.0   
60   Downtown Toronto -79.382900             3.0   
62   Downtown Toronto -79.382900             3.0   
63       West Toronto -79.429050             3.0   
64       West Toronto -79.381556             3.0   
65        Scarborough -79.263562             3.0   
67        Scarborough -79.262290             3.0   
69         North York -79.412630             3.0   
71       East Toronto -79.290792             3.0   
73   Downtown Toronto -79.380110             3.0   
74   Downtown Toronto -79.381460             3.0   
75       West Toronto -79.434484             3.0   
76       West Toronto -79.416340             3.0   
77       West Toronto -79.451431             3.0   
78        Scarborough -79.291541             3.0   
79        Scarborough -79.282750             3.0   
82         North York -79.402843             3.0   
84       East Toronto -79.296440             3.0   
86   Downtown Toronto -79.379515             3.0   
87   Downtown Toronto -79.378940             3.0   
89         North York -79.475530             3.0   
91         North York -79.558490             3.0   
98       East Toronto -79.385440             3.0   
99         North York -79.408772             3.0   
100        North York -79.408314             3.0   
101              York -79.300671             3.0   
105        North York -79.536170             3.0   
106        North York -79.286051             3.0   
107       Scarborough -79.275900             3.0   
109        North York -79.402607             3.0   
111   Central Toronto -79.402320             3.0   
113              York -79.340290             3.0   
115              York -79.509340             3.0   
116       Scarborough -79.277460             3.0   
117       Scarborough -79.260650             3.0   
119        North York -79.402843             3.0   
120   Central Toronto -79.385359             3.0   
123      West Toronto -79.457383             3.0   
124      West Toronto -79.463649             3.0   
126       Scarborough -79.295876             3.0   
129   Central Toronto -79.401980             3.0   
130   Central Toronto -79.404575             3.0   
131   Central Toronto -79.385440             3.0   
132   Central Toronto -79.392444             3.0   
133      West Toronto -79.451431             3.0   
134      West Toronto -79.448971             3.0   
135       Mississauga -79.644940             3.0   
137         Etobicoke -79.557040             3.0   
140       Scarborough -79.280840             3.0   
141   Central Toronto -79.385359             3.0   
142  Downtown Toronto -79.382900             3.0   
143  Downtown Toronto -79.398640             3.0   
147       Scarborough -79.295876             3.0   
151  Downt

## 6.4. Cluster 4

In [44]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Longitude  Cluster Labels 1st Most Common Venue  \
157  Scarborough -79.184122             4.0   American Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
157                   Zoo       Doctor's Office      Doner Restaurant   

    5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
157   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
157           Escape Room  Ethiopian Restaurant            Event Space